# Figure 2 (Training and evaluating on the same database)

In [1]:
from collections import defaultdict

from mol2ccs.utils import performance_evaluation
import pandas as pd
import seaborn as sns
import matplotlib.gridspec as gridspec
from matplotlib import pyplot as plt
import numpy as np
from utils import SeabornFig2Grid

from scipy.stats import linregress
from sklearn.metrics import mean_absolute_error, root_mean_squared_error

In [2]:
plt.rcParams["figure.dpi"] = 500

In [3]:
pd.options.mode.copy_on_write = True

In [4]:
# CCSBase (train) evaluated on CCSBase (test)
ccsbase_test_mol2ccs_pred = pd.read_parquet(
    "ccs-prediction-outputs/final-experiments-paper/mol2ccs/ccsbase_test_3d_pred.parquet"
)

ccsbase_test_graphccs_pred = pd.read_parquet(
    "ccs-prediction-outputs/final-experiments-paper/graphccs/v2-graphccs-ccsbase-test-predictions.parquet"
)

ccsbase_test_sigmaccs_pred = pd.read_parquet(
    "ccs-prediction-outputs/final-experiments-paper/sigmaccs-old/results/ccsbase_test_3d_pred.parquet"
)

# # Metlin train evaluated on Metlin test
metlin_test_mol2ccs_pred = pd.read_parquet(
    "ccs-prediction-outputs/final-experiments-paper/mol2ccs/metlin_test_3d_pred.parquet"
)

metlin_test_graphccs_pred = pd.read_parquet(
    "ccs-prediction-outputs/final-experiments-paper/graphccs/v2-graphccs-metlin-test-predictions.parquet"
)

metlin_test_sigmaccs_pred = pd.read_parquet(
    "ccs-prediction-outputs/final-experiments-paper/sigmaccs-old/results/metlin_test_3d_pred.parquet"
)

Ensure that the predictions are in the same order as the test set

In [5]:
evaluation_dict = defaultdict(dict)  # metrics
predictions_dict = defaultdict(dict)  # experimental_values, predictions

for i, preds in enumerate(
    [
        ccsbase_test_mol2ccs_pred,
        ccsbase_test_graphccs_pred,
        ccsbase_test_sigmaccs_pred,
        metlin_test_mol2ccs_pred,
        metlin_test_graphccs_pred,
        metlin_test_sigmaccs_pred,
    ]
):
    # MOdel name based on the order of the preds
    name = [
        "ccsbase_test_mol2ccs_pred",
        "ccsbase_test_graphccs_pred",
        "ccsbase_test_sigmaccs_pred",
        "metlin_test_mol2ccs_pred",
        "metlin_test_graphccs_pred",
        "metlin_test_sigmaccs_pred",
    ][i]

    if "mol2ccs" in name:
        model = "mol2ccs"
        experimental_values = preds["ccs"].values
        predictions = preds["pred_ccs"].values

    elif "graphccs" in name:
        model = "graphccs"
        experimental_values = preds["Label"].values
        predictions = preds["predict"].values

    else:
        model = "sigmaccs"
        experimental_values = preds["ccs"].values
        predictions = preds["Predicted CCS"].values

    if "ccsbase_test" in name:
        database = "ccsbase_test"
    elif "metlin_test" in name:
        database = "metlin_test"

    evaluation_dict[model][database] = performance_evaluation(
        predictions, experimental_values, verbose=False
    )[0]

    predictions_dict[model][database] = (experimental_values, predictions)

In [6]:
evaluation_dict[model][database].head(10)

Metric      Value
0                     MAE   4.351378
1                     MSE  36.891812
2                    RMSE   6.073863
3                      R2   0.901014
4        Mean Percent RSD   2.201916
5      Median Percent RSD   1.681421
6         Max Percent RSD  27.895690
7         Min Percent RSD   0.000402
8   Pearson's correlation   0.949217
9  Spearman's correlation   0.941183

In [7]:
def calculate_metrics(x, y):

    mae_original = mean_absolute_error(x, y)
    rmse_original = root_mean_squared_error(x, y)
    r2_original = linregress(x, y).rvalue ** 2

    # median relative error in %
    median_relative_error_original = x - y
    # Absolute value
    median_relative_error_original = (
        np.abs(median_relative_error_original) / np.array(x) * 100
    )

    # Get the median
    median_relative_error_original = np.median(median_relative_error_original)

    return mae_original, rmse_original, r2_original, median_relative_error_original

In [8]:
# Make a function to plot the scatter plot for each model
def plot_scatter(
    x: np.array,
    y: np.array,
    color,
    model_name: str,
    alpha: float = 0.2,
    size: int = 10,
    x_label: bool = True,
    y_label: bool = True,
):

    g = sns.jointplot(
        x=x,
        y=y,
        # add transparency to the points
        alpha=alpha,
        s=size,
        # color
        color=color,
    )

    # set title
    g.fig.suptitle(f"Scatter plot of {model_name} predictions")

    # Add a line to show the perfect correlation
    g.ax_joint.plot(
        [x.min(), y.max()],
        [x.min(), y.max()],
        "k--",
        lw=2,
    )

    g.ax_joint.set_xlabel("Experimental CCS", fontsize=16)
    g.ax_joint.set_ylabel(f"Predicted CCS", fontsize=16)

    if x_label is False:
        g.ax_joint.set_xlabel("")
        # no ticks
        g.ax_joint.set_xticks([])

    if y_label is False:
        g.ax_joint.set_ylabel("")
        g.ax_joint.set_yticks([])

    mae, rmse, r2, mre = calculate_metrics(x, y)

    g.ax_joint.text(
        0.05,
        0.95,
        f"n={len(x):,}\nMAE: {mae:.2f}\nRMSE: {rmse:.2f}\nR2: {r2:.2f}\nMRE: {mre:.2f}%",
        horizontalalignment="left",
        verticalalignment="top",
        transform=g.ax_joint.transAxes,
        fontsize=12,
    )

    return g

In [9]:
fig = plt.figure(figsize=(20, 10))
gs = gridspec.GridSpec(2, 3)

palette = {
    "Mol2CCS": "#b3e2cd",
    "GraphCCS": "#fc8d62",
    "Sigmaccs": "#8da0cb",
}

# Mol2CCS is the first column, GraphCCS is the second column, and Sigmaccs is the third column

# CCSBase (train) evaluated on CCSBase (test) is the first row
_ = SeabornFig2Grid(
    plot_scatter(
        x=predictions_dict["mol2ccs"]["ccsbase_test"][0],
        y=predictions_dict["mol2ccs"]["ccsbase_test"][1],
        model_name="Mol2CCS",
        color=palette["Mol2CCS"],
        x_label=False,
        alpha=0.4,
    ),
    fig,
    gs[0],
)

# GraphCCS
_ = SeabornFig2Grid(
    plot_scatter(
        x=predictions_dict["graphccs"]["ccsbase_test"][0],
        y=predictions_dict["graphccs"]["ccsbase_test"][1],
        model_name="GraphCCS",
        color=palette["GraphCCS"],
        x_label=False,
        y_label=False,
        alpha=0.4,
    ),
    fig,
    gs[1],
)

# Sigmaccs
_ = SeabornFig2Grid(
    plot_scatter(
        x=predictions_dict["sigmaccs"]["ccsbase_test"][0],
        y=predictions_dict["sigmaccs"]["ccsbase_test"][1],
        model_name="Sigmaccs",
        color=palette["Sigmaccs"],
        x_label=False,
        y_label=False,
        alpha=0.4,
    ),
    fig,
    gs[2],
)

# Third row

_ = SeabornFig2Grid(
    plot_scatter(
        x=predictions_dict["mol2ccs"]["metlin_test"][0],
        y=predictions_dict["mol2ccs"]["metlin_test"][1],
        model_name="Mol2CCS",
        color=palette["Mol2CCS"],
        x_label=True,
    ),
    fig,
    gs[3],
)

# GraphCCS
_ = SeabornFig2Grid(
    plot_scatter(
        x=predictions_dict["graphccs"]["metlin_test"][0],
        y=predictions_dict["graphccs"]["metlin_test"][1],
        model_name="GraphCCS",
        color=palette["GraphCCS"],
        x_label=True,
        y_label=False,
    ),
    fig,
    gs[4],
)

# Sigmaccs
_ = SeabornFig2Grid(
    plot_scatter(
        x=predictions_dict["sigmaccs"]["metlin_test"][0],
        y=predictions_dict["sigmaccs"]["metlin_test"][1],
        model_name="Sigmaccs",
        color=palette["Sigmaccs"],
        x_label=True,
        y_label=False,
    ),
    fig,
    gs[5],
)


# Add a super title in each column
for i, title in enumerate(
    [
        "Mol2CCS",
        "GraphCCS",
        "SigmaCCS",
    ]
):
    fig.text(
        0.5 * (0.33 * i + 0.33 * (i + 1)),
        1.02,
        title,
        horizontalalignment="center",
        verticalalignment="top",
        fontsize=30,
    )


gs.tight_layout(fig)

# save the figure
plt.savefig("figure_2.png", dpi=500, bbox_inches="tight")

plt.show()